In [6]:
import xarray as xr
from pathlib import Path
import datetime as dt

In [7]:
exps = ['historical', 'ssp126', 'ssp370', 'ssp585']  # 'hist-nat', 
vars = ['pr', 'tas', 'tasmax', 'tasmin', 'hurs']

In [8]:
locs = {
    'lhr': {'lon': -0.4551, 'lat': 51.4680, 'reason': 'has obs data'},  # London Heathrow
    
    # Student request
    'suffolk': {'lon': 1.057185, 'lat': 52.285113, 'reason': 'student'},
    'pontypridd': {'lon': -3.342, 'lat': 51.602, 'reason': 'student'},

    # Heat Wave Hotspots
    'islamabad': {'lon': 73.0479, 'lat': 33.6844, 'reason': 'heat waves'},
    'phoenix': {'lon': -112.0740, 'lat': 33.4484, 'reason': 'heat waves'},
    'delhi': {'lon': 77.1025, 'lat': 28.7041, 'reason': 'heat waves'},
    'baghdad': {'lon': 44.3661, 'lat': 33.3152, 'reason': 'heat waves'},
    'athens': {'lon': 23.7275, 'lat': 37.9838, 'reason': 'heat waves'},
    'shanghai': {'lon': 121.4737, 'lat': 31.2304, 'reason': 'heat waves and humidity extremes'},

    # High Precipitation Extremes
    'mumbai': {'lon': 72.8777, 'lat': 19.0760, 'reason': 'monsoonal precipitation extremes'},
    'jakarta': {'lon': 106.8456, 'lat': -6.2088, 'reason': 'coastal flooding and precipitation extremes'},
    'new_orleans': {'lon': -90.0715, 'lat': 29.9511, 'reason': 'hurricane precipitation and sea level rise'},
    'dhaka': {'lon': 90.4125, 'lat': 23.8103, 'reason': 'monsoonal precipitation and flood risks'}
}

In [19]:
chunks={
    "time": -1,   # one chunk per file or per experiment
}
var = 'pr'
exp = 'historical'

with xr.open_mfdataset(
    f'MRI/{var}/mri-esm2-0_r1i1p1f1_w5e5_{exp}_{var}_global_daily_*.nc',
    chunks=chunks
) as ds:
    ds = ds
print(ds[var].data.chunks)


((365, 3653, 3652, 3653, 3652, 3652, 3652, 3653, 3652, 3653, 3652, 3653, 3652, 3653, 3652, 3653, 3652, 1461), (360,), (720,))


In [9]:
def t():
    return dt.datetime.now().strftime("%H:%M:%S")

def td(start):
    return (dt.datetime.now() - start).total_seconds()

t_start = dt.datetime.now()

print(f"{t()} START script")
for var in vars:
    print(f"{t()}  START var = {var}")

    for exp in exps:
        print(f"{t()}    START exp = {exp}")
        t_open = dt.datetime.now()

        with xr.open_mfdataset(
            f'MRI/{var}/mri-esm2-0_r1i1p1f1_w5e5_{exp}_{var}_global_daily_*.nc', 
            chunks={'time': -1}
        ) as ds:

            print(f"{t()}    open_mfdataset done (took {td(t_open):.1f}s)")

            for name, loc in locs.items():
                print(f"{t()}      point = {name}")
                t_sel = dt.datetime.now()

                odir = f"../timeseries/{name}/netcdf/{var}/"
                Path(odir).mkdir(parents=True, exist_ok=True)

                tas = ds[var].sel(
                    lat=loc['lat'],
                    lon=loc['lon'],
                    method='nearest'
                ).load()

                print(f"{t()}      sel done (took {td(t_sel):.2f}s)")
                t_nc = dt.datetime.now()

                outpath = f'{odir}/mri-esm2-0_r1i1p1f1_w5e5_{exp}_{var}_{name}_daily.nc'
                tas.to_netcdf(outpath)

                print(f"{t()}      to_netcdf done (took {td(t_nc):.2f}s)")

        print(f"{t()}    END exp = {exp}  (total {td(t_open):.1f}s)")

    print(f"{t()}  CSV conversion for var = {var}")
    for name, loc in locs.items():
        idir = f"../timeseries/{name}/netcdf/{var}/"
        odir = f"../timeseries/{name}/csv/{var}/"
        Path(odir).mkdir(parents=True, exist_ok=True)

        for exp in exps:
            t_csv = dt.datetime.now()

            da = xr.open_dataarray(
                f'{idir}/mri-esm2-0_r1i1p1f1_w5e5_{exp}_{var}_{name}_daily.nc'
            )

            da.to_dataframe().to_csv(
                f'{odir}/mri-esm2-0_r1i1p1f1_w5e5_{exp}_{var}_{name}_daily.csv'
            )

            print(f"{t()}    CSV {name} {exp} done (took {td(t_csv):.2f}s)")

    print(f"{t()}  END var = {var}")
print(f"{t()} END script (took {td(t_start):.2f}s)")

23:34:12  START var = hurs
23:34:12    START exp = ssp585
23:34:12    open_mfdataset done (took 0.2s)
23:34:12      point = lhr


KeyboardInterrupt: 

In [7]:
print('Done')

Done
